In [1]:
import sys
import os
import random
import gc
import time
import torch
import numpy as np
import pandas as pd
import ast
from tqdm import tqdm
from scipy.sparse import csr_matrix
import itertools
from scipy.stats import spearmanr, pearsonr, kendalltau, rankdata
from sklearn.metrics import ndcg_score
from sklearn.metrics import root_mean_squared_error
from transformers import AutoModelForCausalLM, AutoTokenizer
from accelerate import Accelerator
import nltk
nltk.download('punkt')
from nltk.tokenize import sent_tokenize

current_dir = os.getcwd()
parent_dir = os.path.abspath(os.path.join(current_dir, '..'))
sys.path.append(parent_dir)
from SHapRAG import *
#os.environ["CUDA_VISIBLE_DEVICES"] = "0" 

/globalsc/users/e/k/ekuzmenk/LLMX/shaprag/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[nltk_data] Downloading package punkt to
[nltk_data]     /home/ulb/code_wit/ekuzmenk/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
#df=pd.read_json("../data/musique/musique_ans_v1.0_train.jsonl", lines=True)
df= pd.read_csv("../scripts/nq_2_positives.csv",index_col=False)

In [3]:
from os import getenv
from dotenv import load_dotenv

load_dotenv()
HF_TOKEN = os.getenv('HF_TOKEN')

In [4]:
SEED = 42
# Initialize Accelerator
accelerator_main = Accelerator(mixed_precision="fp16")

# Load Model
if accelerator_main.is_main_process:
    print("Main Script: Loading model...")
# model_path = "mistralai/Mistral-7B-Instruct-v0.3"
model_path = "meta-llama/Llama-3.1-8B-Instruct"
# model_path = "Qwen/Qwen2.5-3B-Instruct"


model_cpu = AutoModelForCausalLM.from_pretrained(
    model_path,
    torch_dtype=torch.float16,
    token=HF_TOKEN
)
tokenizer = AutoTokenizer.from_pretrained(model_path, token=HF_TOKEN)
if tokenizer.pad_token is None:
    tokenizer.pad_token = tokenizer.eos_token
    model_cpu.config.pad_token_id = tokenizer.pad_token_id
    if hasattr(model_cpu, 'generation_config') and model_cpu.generation_config is not None:
        model_cpu.generation_config.pad_token_id = tokenizer.pad_token_id

if accelerator_main.is_main_process:
    print("Main Script: Preparing model with Accelerator...")
prepared_model = accelerator_main.prepare(model_cpu)
unwrapped_prepared_model = accelerator_main.unwrap_model(prepared_model)
unwrapped_prepared_model.eval()
if accelerator_main.is_main_process:
    print("Main Script: Model prepared and set to eval.")

# Define utility cache

accelerator_main.wait_for_everyone()

/globalsc/users/e/k/ekuzmenk/LLMX/shaprag/lib/python3.11/site-packages/accelerate/accelerator.py:469: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)


Main Script: Loading model...


Loading checkpoint shards: 100%|█████████████████████████████████████████████████████████████████████████████████| 4/4 [00:08<00:00,  2.15s/it]


Main Script: Preparing model with Accelerator...
Main Script: Model prepared and set to eval.


In [5]:
all_sents = []
for i in range(len(df.question)):
    n = 0
    docs=ast.literal_eval(df.context[i])
    doc_sents = []
    for j in range(len(docs)):
        sents = nltk.sent_tokenize(docs[j])
        new_sents = []
        for s in range(len(sents)):
            #new_sents.append(str(n + s) + '-' + str(j) + '-' + sents[s])
            new_sents.append(sents[s])
        n += len(sents)
        doc_sents.append(new_sents)
    flat_doc_sents = [
    x
    for xs in doc_sents
    for x in xs
]
    all_sents.append(flat_doc_sents)
df['Sentences'] = all_sents

In [6]:
df.head(10)

question  \
0        total number of death row inmates in the us   
1         big little lies season 2 how many episodes   
2               who sang waiting for a girl like you   
3     where do you cross the arctic circle in norway   
4    who is the main character in green eggs and ham   
5          do veins carry blood to the heart or away   
6  who played charlie bucket in the original char...   
7                    what is 1 radian in terms of pi   
8         when does season 5 of bates motel come out   
9  how many episodes are in series 7 game of thrones   

                                             context                   answer  \
0  ['on death row in the United States on January...                    2,718   
1  ['series garnered several accolades. It receiv...                    seven   
2  ['Waiting for a Girl Like You "Waiting for a G...                Foreigner   
3  ['Arctic Norway Arctic Norway () comprises the...              Saltfjellet   
4  ['Green Eggs and Ham Green Eggs and Ham is a c...                 Sam-I-am   
5  ['Vein Veins are blood vessels that carry bloo...                       to   
6  ['Peter Ostrum Peter Gardner Ostrum (; born No...  Peter Gardner[4] Ostrum   
7  ['and the integral computes the area between t...                     1/2π   
8  ['Bates Motel (season 5) The fifth and final s...        February 20, 2017   
9  ['Game of Thrones (season 7) The seventh and p...                    seven   

                                           Sentences  
0  [on death row in the United States on January ...  
1  [series garnered several accolades., It receiv...  
2  [Waiting for a Girl Like You "Waiting for a Gi...  
3  [Arctic Norway Arctic Norway () comprises the ...  
4  [Green Eggs and Ham Green Eggs and Ham is a ch...  
5  [Vein Veins are blood vessels that carry blood...  
6  [Peter Ostrum Peter Gardner Ostrum (; born Nov...  
7  [and the integral computes the area between th...  
8  [Bates Motel (season 5) The fifth and final se...  
9  [Game of Thrones (season 7) The seventh and pe...

In [6]:
# NEW VERSION
num_questions_to_run=50
k_values = [1,2,3,4,5]
all_results=[]
LDSs=[]
r2_fm=[]
r2_cc=[]

for i in tqdm(range(num_questions_to_run), disable=not accelerator_main.is_main_process):
    query = df.question[i]
    if accelerator_main.is_main_process:
        print(f"\n--- Question {i+1}/{num_questions_to_run}: {query[:60]}... ---")

    docs=df.Sentences[i]
    #docs=ast.literal_eval(df.context[i])
    utility_cache_base_dir = f"../Experiment_data/NQ/{model_path.split('/')[1]}/sentences"
    #utility_cache_base_dir = f"../Experiment_data/musique"
    utility_cache_filename = f"utilities_q_idx{i}.pkl" # More robust naming
    current_utility_path = os.path.join(utility_cache_base_dir, utility_cache_filename)
    
    if accelerator_main.is_main_process: # Only main process creates directories
        os.makedirs(os.path.dirname(current_utility_path), exist_ok=True)
    
    # Initialize Harness
    print('Initializing harness...')
    harness = ContextAttribution(
        items=docs,
        query=query,
        prepared_model=prepared_model,
        prepared_tokenizer=tokenizer,
        accelerator=accelerator_main,
        utility_cache_path=current_utility_path
    )
    print(f'Response: {harness.target_response}')
    print(f'GT: {df.answer[i]}')
    # Compute metrics
    results_for_query = {}
    if accelerator_main.is_main_process:
        m_samples_map = {"L": 364} 
        # m_samples_map = {"L": 128, "XL":256, "XXL":512} 
        T_iterations_map = {"L":40, "XL":50, "XXL":60} 

        for size_key, num_s in m_samples_map.items():
            if 2**len(docs) < num_s and size_key != "L":
                actual_samples = max(1, 2**len(docs)-1 if 2**len(docs)>0 else 1)
            else:
                actual_samples = num_s

            if actual_samples > 0:
                results_for_query[f"ContextCite{actual_samples}"], model_cc = harness.compute_contextcite(num_samples=actual_samples, seed=SEED)
                attributions, ints=harness.compute_spex(sample_budget=actual_samples,max_order=2)
                results_for_query[f"FBII{actual_samples}"]=attributions['fbii']
                results_for_query[f"Spex{actual_samples}"]=attributions['fourier']
                results_for_query[f"FSII{actual_samples}"]=attributions['fsii']
                results_for_query[f"FM_WeightsD{actual_samples}"], F, modelfm = harness.compute_wss(num_samples=actual_samples, seed=SEED, sampling="kernelshap",sur_type="fm", utility_mode="divergence_utility")
                results_for_query[f"FM_Weights{actual_samples}"], F, modelfm = harness.compute_wss(num_samples=actual_samples, seed=SEED, sampling="kernelshap",sur_type="fm")
                # results_for_query[f"BetaShap{actual_samples}"] = harness.compute_beta_shap(num_iterations_max=T_iterations_map[size_key], beta_a=16, beta_b=1, max_unique_lookups=actual_samples, seed=SEED)
                # results_for_query[f"TMC{actual_samples}"] = harness.compute_tmc_shap(num_iterations_max=T_iterations_map[size_key], performance_tolerance=0.001, max_unique_lookups=actual_samples, seed=SEED)

        results_for_query["LOO"] = harness.compute_loo()
        results_for_query["ARC-JSD"] = harness.compute_arc_jsd()

        prob_topk = harness.evaluate_topk_performance(
                                                results_for_query, 
                                                k_values, 
                                                utility_type="probability"
                                            )

        div_topk = harness.evaluate_topk_performance(
                                            results_for_query, 
                                            k_values, 
                                            utility_type="divergence"
                                        )
        # for doc level for now, needs annotation for sentences
        cc_precision = harness.precision([0, 1], results_for_query[f"ContextCite{actual_samples}"])
        fm_precision = harness.precision([0, 1], results_for_query[f"FM_Weights{actual_samples}"])
        fmw_precision = harness.precision([0, 1], results_for_query[f"FM_WeightsD{actual_samples}"])
        fbi_precision = harness.precision([0, 1], results_for_query[f"FBII{actual_samples}"])


        LDS = {}
        for i in results_for_query:
            if "FM" in i:
                calculate_LDS = {i:harness.lds(results_for_query[i], 30, utl=True, model=modelfm)}
                LDS.update(calculate_LDS)
            else:
                calculate_LDS = {i:harness.lds(results_for_query[i], 30)}
                LDS.update(calculate_LDS)
        LDS = [{i:harness.lds(results_for_query[i], 30)} for i in results_for_query]

        results_for_query["topk_probability"] = prob_topk
        results_for_query["topk_divergence"] = div_topk
        results_for_query["LDS"] = LDS
        harness.save_utility_cache(current_utility_path)
        
        all_results.append(results_for_query)

  0%|                                                                                                                   | 0/50 [00:00<?, ?it/s]


--- Question 1/50: total number of death row inmates in the us... ---
Initializing harness...
Main Process: Attempting to load utility cache from ../Experiment_data/NQ/Llama-3.1-8B-Instruct/sentences/utilities_q_idx0.pkl...
Successfully loaded 779 cached utility entries.
Response: As of November 1999, there are 956 death convicts at the National Bilibid Prisons and at the Correctional Institute for Women.
GT: 2,718



Computing utilities for ContextCite: 100%|███████████████████████████████████████████████████████████████| 364/364 [00:00<00:00, 375209.30it/s]


100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████| 45/45 [00:50<00:00,  1.12s/it]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

Computing utilities for WSS (kernelshap): 100%|██████████████████████████████████████████████████████████| 338/338 [00:00<00:00, 315951.58it/s]

Computing utilities for WSS (kernelshap): 100%|██████████████████████████████████████████████████████████| 338/338 [00:00<00:00, 354773.46it/s]

LOO Calls (logit-prob): 100%|██████████████████████████████████████████████████████████████████████████████| 57/57 [00:00<00:00, 164200.09it/s]

  2%|██                                                                                                       | 1/50 [01:24<1:09:22, 84.95s/it]

Main Process: Saving 779 utility entries to ../Experiment_data/NQ/Llama-3.1-8B-Instruct/sentences/utilities_q_idx0.pkl...
Save complete.

--- Question 2/50: big little lies season 2 how many episodes... ---
Initializing harness...
Main Process: Attempting to load utility cache from ../Experiment_data/NQ/Llama-3.1-8B-Instruct/sentences/utilities_q_idx1.pkl...
Successfully loaded 791 cached utility entries.
Response: 7
GT: seven


...

Main Process: Saving 773 utility entries to ../Experiment_data/NQ/Llama-3.1-8B-Instruct/sentences/utilities_q_idx48.pkl...
Save complete.

--- Question 50/50: who sang the song every breath you take... ---
Initializing harness...
Response: The Police.
GT: The Police



100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████| 45/45 [00:51<00:00,  1.13s/it]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

0it [00:00, ?it/s]

Computing utilities for WSS (kernelshap):   0%|                                                                        | 0/344 [00:00<?, ?it/s]

  (Divergence Utility) Caching baseline token distributions for full context...



Computing utilities for WSS (kernelshap): 100%|██████████████████████████████████████████████████████████████| 344/344 [00:50<00:00,  6.85it/s]

Computing utilities for WSS (kernelshap): 100%|██████████████████████████████████████████████████████████████| 344/344 [00:49<00:00,  6.95it/s]

LOO Calls (logit-prob): 100%|██████████████████████████████████████████████████████████████████████████████████| 64/64 [00:08<00:00,  7.33it/s]

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [2:25:21<00:00, 174.42s/it]

Main Process: Saving 794 utility entries to ../Experiment_data/NQ/Llama-3.1-8B-Instruct/sentences/utilities_q_idx49.pkl...
Save complete.


In [7]:
methods = [f'ContextCite{actual_samples}', f'FM_Weights{actual_samples}',f'FM_WeightsD{actual_samples}',f'Spex{actual_samples}',f'FBII{actual_samples}',f'FSII{actual_samples}', 'LOO', 'ARC-JSD']

# Initialize lists
topk_probs = {method: [] for method in methods}
topk_divs = {method: [] for method in methods}
LDSs = {method: [] for method in methods}

# Collect values
for ind, entry in enumerate(all_results):
    for method in methods:
        topk_probs[method].append(entry['topk_probability'][method][3])
        topk_divs[method].append(entry['topk_divergence'][method][3])
        for d in entry['LDS']:
            if method in d and not np.isnan(d[method]):
                LDSs[method].append(d[method])
                break
        

# Compute means
mean_topk_probs = {method: np.mean(topk_probs[method]) for method in methods}
mean_topk_divs = {method: np.mean(topk_divs[method]) for method in methods}
mean_LDSs = {method: np.mean(LDSs[method]) for method in methods}

print("Mean topk_probability:", mean_topk_probs)
print("Mean topk_divergence:", mean_topk_divs)
print("Mean LDS:", mean_LDSs)

Mean topk_probability: {'ContextCite364': 11.87266467353329, 'FM_Weights364': 11.232420057263225, 'FM_WeightsD364': 10.670906675923616, 'Spex364': 12.551235888209193, 'FBII364': 12.43670495113358, 'FSII364': 12.43670495113358, 'LOO': 10.209360985066741, 'ARC-JSD': 11.18596002439037}
Mean topk_divergence: {'ContextCite364': 1.4231881811443678, 'FM_Weights364': 1.3669730568168712, 'FM_WeightsD364': 1.477624880192605, 'Spex364': 1.5508743182194544, 'FBII364': 1.5715239935201728, 'FSII364': 1.5715239935201728, 'LOO': 1.2295310488616673, 'ARC-JSD': 1.4662313626771435}
Mean LDS: {'ContextCite364': 0.7137408912396994, 'FM_Weights364': 0.5916351501668521, 'FM_WeightsD364': 0.636182424916574, 'Spex364': 0.7221959372590794, 'FBII364': 0.7041221685444364, 'FSII364': 0.7041221685444364, 'LOO': 0.44809425438696054, 'ARC-JSD': 0.7362402669632925}


In [21]:
type(mean_LDSs['ContextCite364'])

numpy.float64

In [69]:
query_to_explore = 10
print('Question:', df.question[query_to_explore])
print('Answer:', df.answer[query_to_explore])
docs = ast.literal_eval(df.context[query_to_explore])
for doc in docs:
    print('--------------------')
    print(doc)

Question: who is next in line to be the monarch of england
Answer: Charles, Prince of Wales
--------------------
Catholics are eligible. Queen Elizabeth II is the sovereign, and her heir apparent is her eldest son, Charles, Prince of Wales. Next in line after him is Prince William, Duke of Cambridge, the Prince of Wales's elder son. Third in line is Prince George, the eldest child of the Duke of Cambridge, followed by his sister, Princess Charlotte and younger brother, Prince Louis. Sixth in line is Prince Harry, Duke of Sussex, the younger son of the Prince of Wales. Under the Perth Agreement, which came into effect in 2015, only the first six in line of succession require the
--------------------
The Act required that the regent should be the next person in the line of succession who was: The Counsellors of State were to consist of: Thus, at the time of the passing of the Act, Prince Henry, Duke of Gloucester would have become Regent in the event that King George VI died while The Pr

In [70]:
result_to_observe = all_results[query_to_explore]
fm_weights = result_to_observe['FM_Weights512']
cc_weights = result_to_observe['ContextCite512']
loo_weights = result_to_observe['LOO']
jsd_weights = result_to_observe['ARC-JSD']
print('FM ranking: ', np.argsort(fm_weights)[::-1])
print('CC ranking: ', np.argsort(cc_weights)[::-1])
print('LOO ranking: ', np.argsort(loo_weights)[::-1])
print('JSD ranking: ', np.argsort(jsd_weights)[::-1])

FM ranking:  [0 6 5 9 7 3 8 2 4 1]
CC ranking:  [0 6 7 5 2 9 3 8 4 1]
LOO ranking:  [0 9 8 6 7 5 2 4 3 1]
JSD ranking:  [0 8 1 2 7 6 5 9 4 3]


In [24]:
import json
import copy
all_results_json = copy.deepcopy(all_results)

    # Recursively convert NumPy arrays to lists
def convert_numpy_to_list(obj):
    if isinstance(obj, np.ndarray):
        return obj.tolist()
    elif isinstance(obj, (np.integer, np.floating, np.bool_)):
        # Convert NumPy scalar types to Python native types
        return obj.item()
    elif isinstance(obj, dict):
        return {k: convert_numpy_to_list(v) for k, v in obj.items()}
    elif isinstance(obj, list):
            return [convert_numpy_to_list(elem) for elem in obj]
    else:
        return obj

converted_all_results = convert_numpy_to_list(all_results_json)

with open('NQ_sents_25_FM4_512.json', 'w') as f:
    json.dump(converted_all_results, f, indent=4)

In [12]:
import matplotlib.pyplot as plt
def plot_bar_chart(data_dict, title="Averaged R2 for NQ sent-level, FM20",
                   x_label="Methods", y_label="R2"):

    plot_data = []
    for key, value in data_dict.items():
        if not math.isnan(value):
            plot_data.append((key, value))
        else:
            print(f"Skipping '{key}' for plotting as its value is NaN.")

    if not plot_data:
        print("No valid numeric data to plot after filtering NaNs.")
        return

    # --- NEW: Sort the data ---
    # Sort by the value (index 1 of the tuple), in descending order
    plot_data.sort(key=lambda item: item[1], reverse=True)

    # Unpack sorted data into separate lists for plotting
    labels = [item[0] for item in plot_data]
    values = [item[1] for item in plot_data]
    
    # --- NEW: Define a list of colors ---
    # You can customize this list with any valid matplotlib color names or hex codes.
    colors = ['#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd', '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf']
    # If you have more bars than colors, you can use matplotlib.cm for a colormap:
    # import matplotlib.cm as cm
    # colors = cm.viridis(np.linspace(0, 1, len(labels)))

    plt.figure(figsize=(12, 7))
    # --- NEW: Pass the list of colors to plt.bar ---
    bars = plt.bar(labels, values, color=colors[:len(labels)]) # Slice to match number of bars

    # Add titles and labels
    plt.xlabel(x_label, fontsize=12)
    plt.ylabel(y_label, fontsize=12)
    plt.title(title, fontsize=14)

    # Rotate x-axis labels if they are long to prevent overlap
    plt.xticks(rotation=45, ha='right', fontsize=10) # 'ha' is horizontal alignment

    # Add value labels on top of the bars
    for bar in bars:
        yval = bar.get_height()
        plt.text(bar.get_x() + bar.get_width()/2, yval + 0.01, # Position text slightly above bar
                 round(yval, 4), # Format value to 4 decimal places
                 ha='center', va='bottom', fontsize=9)

    # Add a grid for easier reading of values
    plt.grid(axis='y', linestyle='--', alpha=0.7)

    # Adjust layout to prevent labels from being cut off
    plt.tight_layout()

    # Display the plot
    #plt.show()
    plt.savefig(f'nq_sents_100_fm20_R2_2307.png')

plot_bar_chart(averaged_R2)

In [16]:
import matplotlib.pyplot as plt
import numpy as np
import math # For handling potential NaN values if they were in the input

# --- Plotting Function for Grouped Bar Chart ---
def plot_grouped_bar_chart(data_for_plotting, title="Divergence Climb",
                           x_label="Methods", y_label="Averaged Divergence Climb"):
    """
    Draws a grouped bar chart for the given nested dictionary data.

    Args:
        data_for_plotting (dict): A dictionary where keys are metric names,
                                  and values are dictionaries containing numeric
                                  values for categories like '1' and '2'.
                                  e.g., {'MetricA': {'1': 0.1, '2': 0.2}}
        title (str): The title of the plot.
        x_label (str): Label for the x-axis.
        y_label (str): Label for the y-axis.
    """
    if not data_for_plotting:
        print("No data to plot. The input dictionary is empty.")
        return

    # Extract metric names and ensure a consistent order (alphabetical for clarity)
    metric_names = sorted(data_for_plotting.keys())

    # Prepare data for plotting
    values_cat1 = []
    values_cat2 = []
    
    # Store labels for the actual metrics being plotted (in case some have NaNs)
    plot_metric_labels = []

    for metric in metric_names:
        cat_data = data_for_plotting[metric]
        val1 = cat_data.get('1', float('nan')) # Use .get() to handle missing keys
        val2 = cat_data.get('2', float('nan'))

        # Only include metrics where at least one category has a valid number
        if (isinstance(val1, (int, float)) and not math.isnan(val1)) or \
           (isinstance(val2, (int, float)) and not math.isnan(val2)):
            values_cat1.append(val1 if (isinstance(val1, (int, float)) and not math.isnan(val1)) else 0)
            values_cat2.append(val2 if (isinstance(val2, (int, float)) and not math.isnan(val2)) else 0)
            plot_metric_labels.append(metric)
        else:
            print(f"Skipping metric '{metric}' as both '1' and '2' values are NaN or non-numeric.")


    if not plot_metric_labels:
        print("No valid data points found to plot after processing categories.")
        return

    # Set up positions for the bars
    bar_width = 0.35
    index = np.arange(len(plot_metric_labels)) # The x locations for the groups

    plt.figure(figsize=(14, 8)) # Adjust figure size

    # Plotting the bars
    bar1 = plt.bar(index - bar_width/2, values_cat1, bar_width, label='1', color='skyblue')
    bar2 = plt.bar(index + bar_width/2, values_cat2, bar_width, label='2', color='lightcoral')

    # Add labels, title, and legend
    plt.xlabel(x_label, fontsize=14)
    plt.ylabel(y_label, fontsize=14)
    plt.title(title, fontsize=16)
    plt.xticks(index, plot_metric_labels, rotation=45, ha='right', fontsize=12) # Set metric labels at group center
    plt.yticks(fontsize=12)
    plt.legend(fontsize=12)

    # Add value labels on top of the bars
    def autolabel(bars):
        for bar in bars:
            height = bar.get_height()
            plt.text(bar.get_x() + bar.get_width()/2, height + 0.005, # Position text slightly above bar
                     f'{height:.4f}', # Format value to 4 decimal places
                     ha='center', va='bottom', fontsize=9, rotation=0)

    autolabel(bar1)
    autolabel(bar2)

    plt.grid(axis='y', linestyle='--', alpha=0.7)
    plt.tight_layout() # Adjust layout to prevent labels from being cut off
    #plt.show()
    plt.savefig(f'nq_sents_100_fm20_div_drop_2307.png')

plot_grouped_bar_chart(div_drops)

In [9]:
[i for i in results_for_query]

['ContextCite100',
 'FM_Shap100',
 'FM_Weights100',
 'BetaShap100',
 'TMC100',
 'LOO',
 'ARC-JSD',
 'topk_probability',
 'topk_divergence']

In [10]:
df.question[9]

'how many episodes are in series 7 game of thrones'

In [11]:
harness._generate_sampled_ablations(4, sampling_method='uniform', seed=2)

In [12]:
df.context[9]

'[\'Game of Thrones (season 7) The seventh and penultimate season of the fantasy drama television series "Game of Thrones" premiered on HBO on July 16, 2017, and concluded on August 27, 2017. Unlike previous seasons that consisted of ten episodes each, the seventh season consisted of only seven. Like the previous season, it largely consisted of original content not found in George R. R. Martin\\\'s "A Song of Ice and Fire" series, while also incorporating material Martin revealed to showrunners about the upcoming novels in the series. The series was adapted for television by David Benioff and D. B. Weiss.\', \'Bender, who worked on the show\\\'s sixth season, said that the seventh season would consist of seven episodes. Benioff and Weiss stated that they were unable to produce 10 episodes in the show\\\'s usual 12 to 14 month time frame, as Weiss said "It\\\'s crossing out of a television schedule into more of a mid-range movie schedule." HBO confirmed on July 18, 2016, that the sevent

In [37]:
docs[6]

'genuine, though very obscure, saying, "only fools and horses work for a living", which had its origins in 19th-century American vaudeville. "Only Fools and Horses" had also been the title of an episode of "Citizen Smith", and Sullivan liked the expression and thought it was suited to the new sitcom. He also thought longer titles would attract attention. He was first overruled on the grounds that the audience would not understand the title, but he eventually got his way. Filming of the first series began in May 1981, and the first episode, "Big Brother", was transmitted on BBC One at\''

In [15]:
all_results[0]

{'ContextCite100': array([ 9.42799874e+00,  4.95333848e+00,  1.54510382e-01, -1.18733185e+00,
        -1.97362536e-01, -1.63601493e-03, -4.20977587e-01, -1.71711992e+00,
         5.13743546e-01, -3.61054749e-01]),
 'FM_Shap100': array([10.32068284,  5.69851447,  0.11906173, -0.44636073, -0.88331575,
        -1.00641049, -0.22007863, -0.79765982,  0.29558806, -0.81720759]),
 'FM_Weights100': array([10.32068284,  5.69851447,  0.11906173, -0.44636073, -0.88331575,
        -1.00641049, -0.22007863, -0.79765982,  0.29558806, -0.81720759]),
 'BetaShap100': array([12.18496471,  6.09588892,  0.22350156,  0.12756782, -0.06228456,
         0.05961801,  0.48444461, -0.42519495,  0.84019263, -0.43572434]),
 'TMC100': array([ 9.96529419,  5.98631053, -0.16527917, -0.53574083, -0.08729146,
        -0.09466684,  0.01608808, -0.76350622,  0.2977114 , -0.34037049]),
 'LOO': array([12.21575832,  8.61024857,  1.24591446,  0.25884056, -0.06205273,
         0.06636238,  0.56908131, -0.40280247,  0.83529949

In [16]:
F

array([[ 0.        , -2.71718673,  2.64412498,  0.42945254,  0.83703511,
         0.81296934,  2.79770344, -0.70547725, -1.78606628, -1.45755979],
       [-2.71718673,  0.        , -1.55238252,  0.47399397,  0.30587813,
        -1.0472584 , -3.32381804, -0.22556415,  1.52053671,  2.70219414],
       [ 2.64412498, -1.55238252,  0.        , -0.05849546,  0.24429583,
         1.2087218 , -1.96988449,  0.43088249,  1.2081562 ,  1.73971653],
       [ 0.42945254,  0.47399397, -0.05849546,  0.        ,  0.45773645,
         0.56765182,  0.01962721, -0.01922445,  0.25747797, -0.84770228],
       [ 0.83703511,  0.30587813,  0.24429583,  0.45773645,  0.        ,
         0.23349889,  0.07346147, -0.04195382,  0.03793556, -0.31164835],
       [ 0.81296934, -1.0472584 ,  1.2087218 ,  0.56765182,  0.23349889,
         0.        ,  0.17034947,  0.01708509,  0.06055724, -0.52206366],
       [ 2.79770344, -3.32381804, -1.96988449,  0.01962721,  0.07346147,
         0.17034947,  0.        , -0.15618031

In [17]:
all_subsets = list(itertools.product([0, 1], repeat=4))

In [18]:
sampled_tuples = harness._generate_sampled_ablations(10, sampling_method='uniform', seed=2)

In [17]:
d = {}
type(d)

dict

In [18]:
import matplotlib.pyplot as plt

for result in range(len(all_results)):
    method_scores = {}
    for method, scores in all_results[result].items():
        if scores is not None and type(scores) is not dict:
            print(method, scores)
            method_scores[method] = np.round(scores, 4)

    for method, scores in method_scores.items():
        plt.figure(figsize=(10, 4))
        plt.bar(range(len(scores)), scores, color='skyblue')
        plt.title(f"Approximate Scores: {method}")
        plt.xlabel("Index")
        plt.ylabel("Score")
        plt.grid(axis='y', linestyle='--', alpha=0.7)
        plt.xticks(range(len(scores)))
        plt.tight_layout()
        plt.savefig(f'nq_doc_plots/{result}_{method}.png')

ContextCite100 [ 9.42799874e+00  4.95333848e+00  1.54510382e-01 -1.18733185e+00
 -1.97362536e-01 -1.63601493e-03 -4.20977587e-01 -1.71711992e+00
  5.13743546e-01 -3.61054749e-01]
FM_Shap100 [10.32068284  5.69851447  0.11906173 -0.44636073 -0.88331575 -1.00641049
 -0.22007863 -0.79765982  0.29558806 -0.81720759]
FM_Weights100 [10.32068284  5.69851447  0.11906173 -0.44636073 -0.88331575 -1.00641049
 -0.22007863 -0.79765982  0.29558806 -0.81720759]
BetaShap100 [12.18172271  7.73213164  0.78913852  0.1642193  -0.06000717  0.05865822
  0.56100273 -0.43111163  0.83715638 -0.46782496]
TMC100 [ 9.96529419  5.98631053 -0.16527917 -0.53574083 -0.08729146 -0.09466684
  0.01608808 -0.76350622  0.2977114  -0.34037049]
LOO [12.21575832  8.61024857  1.24591446  0.25884056 -0.06205273  0.06636238
  0.56908131 -0.40280247  0.83529949 -0.49150467]
ARC-JSD [ 0.34588716 10.75895722  0.03822068  0.01981782  0.03414572  0.03501194
  0.05906658  0.02726513  0.04695243  0.04338138]
ContextCite100 [ 0.53418168

/localsc/ekuzmenk/61547/ipykernel_3201918/1415687491.py:11: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`). Consider using `matplotlib.pyplot.close()`.
  plt.figure(figsize=(10, 4))
